---
**Примеры Телеграм ботов с возможностью преобразования текста в речь (TTS), речи в текст (STT, ASR) и речи в речь**

В разделе `Overview of stages` приведены этапы работы бота по отдельности для запуска в Colab или Jupyter,в разделе `Telegram Bots` приведены два примера готовых ботов:

1) Бот который просто генерирует текст с помощью LLM в ответ на любой текст

2) Бот который принимает на вход голосовое или текст, и отвечает текстом и голосовым сообщением с ответом, сгенерированным LLM

Репозиторий проекта  
https://github.com/sergey21000/telegram-sst-tts-bot

---

Aiogram  
https://aiogram.dev/  

Aiogram 3 быстрый старт статья  
https://habr.com/ru/articles/732136/  

Телеграм-боты на Python и AIOgram 3   
https://stepik.org/course/120924/info

Текстовый курс Aiogram 3  
https://mastergroosha.github.io/aiogram-3-guide/

Курс Aiogram 3  
https://nztcoder.com/  
https://www.youtube.com/playlist?list=PLRU2Gs7fnCuiwcEDU0AWGkSTawEQpLFPb  

Телеграм бот на python на Aiogram 3  
https://www.youtube.com/playlist?list=PLNi5HdK6QEmWLtb8gh8pwcFUJCAabqZh_  
https://github.com/PythonHubStudio/aiogram-3-course-telegram-bot

Плейлист Aiogram 3  
https://www.youtube.com/playlist?list=PL-kn4reN4eg2Q7L8zn8Lin5BhR35zbRMQ

Курс Aiogram 3  
https://pressanybutton.ru/category/telegram-bot-na-aiogram3/

Статья Telegram бот с offline распознаванием голосовых и генерацией аудио из текста  
https://habr.com/ru/articles/694632/



# Install libs and Imports

Установка библиотек

In [ ]:
%%capture

# aiogram для написания ТГ ботов
# nest_asyncio чтобы асинхронный код работал в колабе (не в колабе не нужна)
# vosk для распознавания речи из текста
# vosk-tts для синтеза речи
# accelerate для работы с моделями HF
# python-dotenv для работы передачи токена бота через переменные окружения

!pip install -q aiogram nest_asyncio vosk vosk-tts python-dotenv

In [ ]:
!pip install llama_cpp_python

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.9/63.9 MB 11.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 3.5 MB/s eta 0:00:00
  Created wheel for llama_cpp_python: filename=llama_cpp_python-0.3.1-cp310-cp310-linux_x86_64.whl size=3485362 sha256=2739c8f856d0cec779681fbcae4831a5957f06a88942e26e71e8ed1e7a5b6018
  Stored in directory: /root/.cache/pip/wheels/f8/b0/a2/f47d952aec7ab061b9e2a345e23a1e1e137beb7891259e3d0c
Successfully built llama_cpp_python


Проверка версий библиотек

In [ ]:
!pip list | grep -P "aiogram|vosk|llama_cpp_python"

aiogram                            3.13.1
llama_cpp_python                   0.3.1
vosk                               0.3.45
vosk-tts                           0.3.56


Если `llama-cpp-python` не ставится в Colab с поддержкой CUDA то попробовать версию ниже

In [ ]:
# !pip install llama-cpp-python==0.90 --extra-index-url https://abetlen.github.io/llama-cpp-python/whl/cu124

Импорты

In [ ]:
import subprocess
import logging
import asyncio
import json
import wave
import zipfile
import urllib.request

from IPython.display import Audio, display
from pathlib import Path

from llama_cpp import Llama
from vosk_tts import Model as ModelTTS, Synth
from vosk import Model as ModelSTT, KaldiRecognizer

# что асинхронный код работал в коллабе (не в колабе не нужно)
import nest_asyncio
nest_asyncio.apply()

# Telegram Bots

## Text-to-Text Bot

**Бот который просто генерирует текст в ответ на любой текст**

In [ ]:
import os
import logging
import asyncio

from aiogram import Bot, Dispatcher, types, F
from aiogram.filters import CommandStart
from aiogram.types import Message
from aiogram.types import FSInputFile, URLInputFile, BufferedInputFile
from aiogram.utils.chat_action import ChatActionSender

# что асинхронный код работал в коллабе (не в колабе не нужно)
import nest_asyncio
nest_asyncio.apply()


# конфигурация логгирования
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s', force=True)

# вариант указания токена для Colab / Jupyter
# токен, полученный у https://t.me/BotFather
BOT_TOKEN = ''

# инициализация бота и диспетчера
bot = Bot(token=BOT_TOKEN)
dp = Dispatcher()


# параметры инициализации модели
MODEL_KWARGS = dict(
    repo_id='bartowski/gemma-2-2b-it-GGUF',  # название репозитория модели на HF
    filename='*8_0.gguf',  # название файла модели из репозитория HF или регулярка для него
    local_dir='models',  # путь куда скачивтаь модель (будет создана папка)
    n_gpu_layers=-1,  # использовать все слои ГПУ если ГПУ доступен
    verbose=False,  # выводить инфо о модели при инициализации (False чтобы ничего не выводить)
)

# инициализация модели для генерации текста моделью в формате GGUF
model = Llama.from_pretrained(**MODEL_KWARGS)
# поддерживает ли модель системный промт
SUPPORT_SYSTEM_ROLE = 'System role not supported' not in model.metadata['tokenizer.chat_template']
# системный промт
SYSTEM_PROMPT = ''

# конфиг для генерации текста
GENERATION_KWARGS = dict(
    temperature=0.2,  # температура для софтмакса
    top_p=0.95,  # сумма вероятностей токенов из которых нужно выбирать следующий токен
    top_k=40,  # из скольки максимально вероятных токенов выбирать следующий токен
    repeat_penalty=1.0,  # штраф модели за повторения
    )


# предупреждение что если мы задали системный промт и если он не поддерживается моделью
if SYSTEM_PROMPT and not SUPPORT_SYSTEM_ROLE:
    logging.warning('System role not supported by this model!')
    print('System role not supported by this model!')


# функция для генерации текста моделью
def generate_text(user_message: str, system_prompt: str, generation_kwargs: dict):
    # формирование входа для модели - список с диалогом юзера и бота
    messages = []
    # добавления системного промта если он есть
    if system_prompt and SUPPORT_SYSTEM_ROLE:
        messages.append({'role': 'system', 'content': system_prompt})
    # добавление ткущего запроса пользователя
    messages.append({'role': 'user', 'content': user_message})
    # генерация ответа моделью
    response = model.create_chat_completion(
        messages=messages,  # входной промт на который надо сгенерировать ответ
        **generation_kwargs,  # параметры генерации
        )
    generated_text = response['choices'][0]['message']['content']
    return generated_text


# если написать боту команду /start то сработает функция (корутина) answer_text
@dp.message(CommandStart())
async def start(message: Message):
    # имитация набора сообщения ботом - внутри должна быть неблокирующая операция, например asyncio.sleep(3)
    async with ChatActionSender(bot=bot, chat_id=message.from_user.id):
        await asyncio.sleep(3)
    # ответить тому кто написал боту текстом с Markdown разметкой
    await message.answer('__Добро пожаловать, введите любой текст для получеиня ответа__', parse_mode="MarkdownV2")


# если написать боту любой текст то сработает функция (корутина) answer_text
# подробнее про фильтры F https://mastergroosha.github.io/aiogram-3-guide/filters-and-middlewares/
@dp.message(F.text)
async def answer_text(message: Message):
    # имитация набора сообщения ботом
    async with ChatActionSender(bot=bot, chat_id=message.from_user.id, action='typing'):
        # сгенерировать текст в отдельном потоке
        generated_text = await asyncio.to_thread(generate_text, message.text, SYSTEM_PROMPT, GENERATION_KWARGS)
    # ответить пользователю
    await message.answer(generated_text)


# главная функция программы
async def main():
    try:
        # игнорировать сообщения, которые были написаны боту, когда он был оффлайн
        await bot.delete_webhook(drop_pending_updates=True)
        logging.info('Бот запущен и готов к работе')
        # старт бота
        await dp.start_polling(bot)
    except Exception as ex:
        logging.error(f'Произошла ошибка: {ex}')
    finally:
        # завершение работы бота
        await bot.session.close()
        logging.info('Бот остановлен')


# старт всей программы
if __name__ == '__main__':
    asyncio.run(main())

2024-10-14 20:55:30,561 - INFO - Бот запущен и готов к работе
2024-10-14 20:55:30,569 - INFO - Start polling
2024-10-14 20:55:30,667 - INFO - Run polling for bot @sdfdsdgdf334dfsdf_bot id=7530574986 - 'Робот'
2024-10-14 20:57:17,343 - INFO - Update id=901212848 is handled. Duration 8977 ms by bot id=7530574986
2024-10-14 20:57:25,502 - WARNING - Received SIGINT signal
2024-10-14 20:57:25,505 - INFO - Polling stopped for bot @sdfdsdgdf334dfsdf_bot id=7530574986 - 'Робот'
2024-10-14 20:57:25,506 - INFO - Polling stopped
2024-10-14 20:57:25,759 - INFO - Бот остановлен


## Speech-to-Speech Bot

**Бот который принимает на вход голосовое или текст, и отвечает текстом и голосовым сообщением с ответом, сгенерированным LLM**

---

**Структура проекта**
 - 📁 `llm_model`
 - 📁 `vosk_models`
 - `.env`
 - `main.py`
 - `config.py`
 - `handlers.py`
 - `middlewares.py`
 - `infer_models.py`
 - `infer_utils.py`
 - `requirements.txt`


---

**Содержимое `requirements.txt`**
```
llama_cpp_python==0.2.90
huggingface-hub==0.24.7
aiogram==3.13.1
vosk==0.3.45
vosk-tts==0.3.56
python-dotenv==1.0.1
```

Содержимое остальных файлов в репозитории https://github.com/sergey21000/telegram-sst-tts-bot

---

**Установка и запуск:**

1) Установка `ffmpeg`
 - *Linux*
```
sudo apt install ffmpeg
```
 - *Windows*
```
 winget install ffmpeg
```

2) Создание и активация виртуального окружения (опционально)

Создание окружения:
 - *Linux*
```
python3 -m venv env
source env/bin/activate
```
 - *Windows*
```
python -m venv env
env\Scripts\activate.bat
```

3) Установка библиотек
 - *с поддержкой CPU*
 ```
 pip install -r requirements.txt --extra-index-url https://abetlen.github.io/llama-cpp-python/whl/cpu
 ```

 - *с поддержкой CUDA 12.4*
 ```
 pip install -r requirements.txt --extra-index-url https://abetlen.github.io/llama-cpp-python/whl/cu124
 ```

4) Конфигурация - установить в переменую `BOT_TOKEN` в файле `.env` токен бота, полученный у https://t.me/BotFather
```
BOT_TOKEN=your_token
```
Опционально - выбрать модель и настроить ее параметры запуска, а так же параметры генерации текста в файле `config.py`  
Модели можно найти на [HuggingFace](https://huggingface.co/models?pipeline_tag=text-generation&sort=trending)

5) Запуск приложения
```
python3 main.py
```
На Windows `python` вместо `python3`

---

---

Весь код бота в одной ячейке для запуска в Colab  
Перед запуском в Colab закинуть файл `.env` с токеном бота илбо установить токен бота в переменную `BOT_TOKEN` в коде ниже

In [ ]:
import os
import subprocess
import logging
import asyncio
import json
import wave
import zipfile
import urllib.request
from pathlib import Path

from aiogram import Bot, Dispatcher, types, F
from aiogram.filters import CommandStart
from aiogram.types import Message, FSInputFile
from aiogram.utils.chat_action import ChatActionSender

from llama_cpp import Llama
from vosk_tts import Model as ModelTTS, Synth
from vosk import Model as ModelSTT, KaldiRecognizer

# что асинхронный код работал в коллабе (убрать при деплое)
import nest_asyncio
nest_asyncio.apply()


# конфигурация логгирования
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s', force=True)


# ======================== ИНИЦИАЛИЗАЦИЯ БОТА ==============================

# вариант указания токена для Colab / Jupyter
# токен, полученный у https://t.me/BotFather
# BOT_TOKEN = ''

# вариант указания токена для деплоя - создать файл .env и положить туда токен бота в переменую BOT_TOKEN
from dotenv import load_dotenv
load_dotenv()

# извлесение токена бота из файла .env
BOT_TOKEN = os.getenv('BOT_TOKEN')
if BOT_TOKEN is None:
    raise Exception('Установите токен бота в переменную BOT_TOKEN в файле .env')

# инициализация бота и диспетчера
bot = Bot(token=BOT_TOKEN)
dp = Dispatcher()


# =========================== МОДЕЛЬ LLM ============================

# параметры инициализации модели
MODEL_KWARGS = dict(
    repo_id='bartowski/gemma-2-2b-it-GGUF',  # название репозитория модели на HF
    filename='*8_0.gguf',  # название файла модели из репозитория HF или регулярка для него
    local_dir='llm_model',  # путь куда скачивтаь модель (будет создана папка)
    n_gpu_layers=-1,  # использовать все слои ГПУ если ГПУ доступен
    verbose=False,  # выводить инфо о модели при инициализации (False чтобы ничего не выводить)
)

# конфиг для генерации текста
GENERATION_KWARGS = dict(
    temperature=0.2,  # температура для софтмакса
    top_p=0.95,  # сумма вероятностей токенов из которых нужно выбирать следующий токен
    top_k=40,  # из скольки максимально вероятных токенов выбирать следующий токен
    repeat_penalty=1.0,  # штраф модели за повторения
)

# инициализация модели для генерации текста моделью в формате GGUF
model = Llama.from_pretrained(**MODEL_KWARGS)
# поддерживает ли модель системный промт
SUPPORT_SYSTEM_ROLE = 'System role not supported' not in model.metadata['tokenizer.chat_template']
# системный промт
SYSTEM_PROMPT = ''
# предупреждение что если мы задали системный промт и если он не поддерживается моделью
if SYSTEM_PROMPT and not SUPPORT_SYSTEM_ROLE:
    logging.warning('System role not supported by this model!')


# ================ МОДЕЛИ РАСПОЗНАВАНИЯ И СИНТЕЗА РЕЧИ ==============

# функция для загрузки и распаковки архивов с моделями STT и TTS
def download_and_extract_zip(url: str, extract_dir: str | Path):
    zip_path, _ = urllib.request.urlretrieve(url)
    with zipfile.ZipFile(zip_path, 'r') as file:
        file.extractall(extract_dir)

# ссылки на архивы с моделями
tts_model_url = 'https://alphacephei.com/vosk/models/vosk-model-tts-ru-0.7-multi.zip'
stt_model_url = 'https://alphacephei.com/vosk/models/vosk-model-small-ru-0.22.zip'

# папка куда распакуются папки из архивов
vosk_models_dir = Path('vosk_models')
tts_model_dir = vosk_models_dir / Path(tts_model_url).stem
stt_model_dir = vosk_models_dir / Path(stt_model_url).stem

# если модели еще не скачаны то загрузить и распаковать
if not Path(stt_model_dir).is_dir() or not Path(tts_model_dir).is_dir():
    print('Загрузка модели TTS')
    download_and_extract_zip(tts_model_url, vosk_models_dir)
    print('Загрузка модели STT')
    download_and_extract_zip(stt_model_url, vosk_models_dir)

# инициализация модели для синтеза речи
model_tts = ModelTTS(model_path=tts_model_dir)
synth = Synth(model_tts)

# инициализация модели для распознавания речи
model_stt = ModelSTT(model_path=str(stt_model_dir))
# частота диксретизации с которой будет работать модель распознавания речи
SAMPLE_RATE = 16000
recognizer = KaldiRecognizer(model_stt, SAMPLE_RATE)


# =============== НАСТРОЙКИ ВЫБОРА ГОЛОСОВ ДЛЯ СИНТЕЗА РЕЧИ ================

# словарь с индексом текущего голоса для синтеза речи (от 0 до 4)
CURR_SPEAKER = {'speaker_index': 2}
# сделать из словаря строку со значениями голосов и их порядковыми номерами
speaker_names = ['Женский 1', 'Женский 2', 'Женский 3', 'Мужской 1', 'Мужской 2']
ALL_SPEAKERS = dict(enumerate(speaker_names))
# инфо для привественного сообщения с номерами и названиями голосов
speakers_info = '\n'.join([f'**{key}**: _{value}_' for key, value in ALL_SPEAKERS.items()])

# формирование привественного сообщения со списком голосов
welcome_message = rf'''
__Привет, это бот помощник, варианты использования:__
1\) Отправь голосовое или текст чтобы получить ответ текстом и голосом
2\) Для изменения голоса отправь число от 0 до 4:
{speakers_info}
'''


# ============== СЛУЖЕБНЫЕ ФУНКЦИИ ==========================

# принимает путь до айдио файла и извлекает из него текст речи
# если речь не обнаружена или еще какая ошибка - возвращает None
def speech_to_text(audio_path: str) -> str:
    wf = wave.open(audio_path, 'rb')
    audio_data = wf.readframes(-1)
    sample_rate = wf.getframerate()
    recognizer.AcceptWaveform(audio_data)
    recognize_text = json.loads(recognizer.FinalResult())['text']
    return recognize_text


# функция для генерации текста моделью
def text_to_text(user_message: str, system_prompt: str, generation_kwargs: dict):
    # формирование входа для модели - список с диалогом юзера и бота
    messages = []
    # добавления системного промта если он есть
    if system_prompt and SUPPORT_SYSTEM_ROLE:
        messages.append({'role': 'system', 'content': system_prompt})
    # добавление ткущего запроса пользователя
    messages.append({'role': 'user', 'content': user_message})
    # генерация ответа моделью
    response = model.create_chat_completion(
        messages=messages,  # входной промт на который надо сгенерировать ответ
        **generation_kwargs,  # параметры генерации
        )
    generated_text = response['choices'][0]['message']['content']
    return generated_text


# преобразует текст в речь, возвращает путь до аудиофайла с речью
# принимает текст а так же порядковый номер голоса
def text_to_speech(generated_text: str, speaker_index: int)-> str:
    audio_path_tts = 'input_voice.wav'
    synth.synth(generated_text, audio_path_tts, speaker_id=speaker_index)
    return audio_path_tts


# преобразует речь текст, генерирует ответ на него и синтезирует новую речь, используя функции выше
def speech_to_speech(
        audio_path: str,
        system_prompt: str,
        generation_kwargs: dict,
        speaker_index: int,
        ) -> tuple[str | None, str | None]:
    recognized_text = speech_to_text(audio_path)
    if recognized_text.strip() == '':
        return None, None
    generated_text = text_to_text(recognized_text, system_prompt, generation_kwargs)
    audio_path_tts = text_to_speech(generated_text, speaker_index)
    return audio_path_tts, generated_text


# конвертация аудио файла с голосовым сообщением из формата ogg в формат wav
def convert_ogg_to_wav(input_file, output_file):
    try:
        subprocess.run(
            ['ffmpeg', '-y', '-i', input_file, '-ar', str(SAMPLE_RATE), output_file],
            check=True,
            capture_output=True,
            text=True
        )
        # logging.info('Конвертация успешна')
        return True
    except subprocess.CalledProcessError as ex:
        logging.error(f'Ошибка при конвертации ogg в wav:\n{ex} \nСообщение ошибки: \n{ex.stderr}')
        return False


# вариант конвертации через python-ffmpeg
# !pip install python-ffmpeg
# from ffmpeg import FFmpeg
# def convert_ogg_to_wav(input_file, output_file):
#     try:
#         ffmpeg = FFmpeg().option('y').input(input_file).output(output_file, ar=str(SAMPLE_RATE))
#         ffmpeg.execute()
#         return True
#     except Exception as ex:
#         logging.error(f'Ошибка при конвертации ogg в wav:\n{ex} \nСообщение ошибки: \n{ex}')
#         return False


# ================= ОБРАБОТЧИКИ СООБЩЕНИЙ ============================

# если отправить боту команду /start, сработает start
@dp.message(CommandStart())
async def start(message: Message):
    # ответить тому кто написал боту текстом с Markdown разметкой
    await message.answer(welcome_message, parse_mode='MarkdownV2')


# если отправить боту число от 0 до 4 то нужно изменить голос для синтеза речи
@dp.message(F.text.in_('01234'))
async def change_speaker(message: types.Message):
    # извлечь предыдущий индекс спикера чтобы отразить его в сообщении
    old_speaker_index = int(CURR_SPEAKER['speaker_index'])
    # обновить словарь новым индексом спикера - это то что написал пользователь боту
    CURR_SPEAKER['speaker_index'] = int(message.text)
    # отправить пользователю текст что голос был успешно изменен
    answer = f'Голос был изменен с `{ALL_SPEAKERS[old_speaker_index]}` на `{ALL_SPEAKERS[CURR_SPEAKER["speaker_index"]]}`'
    await message.answer(answer, parse_mode='MarkdownV2')


# если отправить боту голосовое, сработает from_voice
@dp.message(F.voice)
async def from_voice(message: Message):
    # название файлов голосовых
    ogg_voice_name = 'voice.ogg'
    wav_voice_name = 'voice.wav'

    # голосовые с ТГ имеют расширение .ogg, скачиваем головое на диск
    await bot.download(message.voice, destination=ogg_voice_name)

    # преобразовываем ogg в wav, чтобы сработала библиотека SpeechRecognition
    convert_status = convert_ogg_to_wav(ogg_voice_name, wav_voice_name)
    if convert_status == False:
        await message.answer('Произошла ошибка при конвертации ogg в wav ☹')
        return

    # имитация набора сообщения ботом
    async with ChatActionSender(bot=bot, chat_id=message.from_user.id, action='record_voice'):
        # сгенерировать текст в отдельном потоке
        audio_path_tts, generated_text = await asyncio.to_thread(
            speech_to_speech,
            wav_voice_name,
            SYSTEM_PROMPT,
            GENERATION_KWARGS,
            CURR_SPEAKER['speaker_index'],
            )

    # если что то пошло не так то бот отвечает таким сообщением
    if audio_path_tts is None:
        await message.answer('Не удалось распознать речь ☹')
        return

    # чтобы отправить пользователю любой файл его надо завернуть в FSInputFile()
    audio_file = FSInputFile(audio_path_tts)
    # отвечаем пользователю и текстом и голосовым
    await message.answer(generated_text)
    await message.answer_voice(audio_file)  # можно передать текст к голосовому: caption=generated_text


# если отправить боту любой текст, сработает from_text
@dp.message(F.text)
async def from_text(message: Message):
    # генерация текста ответа
    async with ChatActionSender(bot=bot, chat_id=message.from_user.id, action='typing'):
        generated_text = await asyncio.to_thread(text_to_text, message.text, SYSTEM_PROMPT, GENERATION_KWARGS)

    # переводим сгенерированный текст в речь
    async with ChatActionSender(bot=bot, chat_id=message.from_user.id, action='record_voice'):
        audio_path_tts = await asyncio.to_thread(text_to_speech, generated_text, CURR_SPEAKER['speaker_index'])

    # создаем файл аудио для отправки
    audio_file = FSInputFile(audio_path_tts)
    await message.answer(generated_text)
    await message.answer_voice(audio_file)


# ======================== ЗАПУСК БОТА =====================================

# главная функция программы
async def main():
    try:
        # игнорировать сообщения, которые были написаны боту, когда он был оффлайн
        await bot.delete_webhook(drop_pending_updates=True)
        logging.info('Бот запущен и готов к работе')
        # старт бота
        await dp.start_polling(bot)
    except Exception as ex:
        logging.error(f'Произошла ошибка: {ex}')
    finally:
        # завершение работы бота
        await bot.session.close()
        logging.info('Бот остановлен')


# старт всей программы
if __name__ == '__main__':
    asyncio.run(main())

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:81: UserWarning: 
Access to the secret `HF_TOKEN` has not been granted on this notebook.
You will not be requested again.
Please restart the session if you want to be prompted again.
  warnings.warn(


Загрузка модели TTS
Загрузка модели STT


2024-10-14 21:06:44,311 - INFO - Loading model from vosk_models/vosk-model-tts-ru-0.7-multi
2024-10-14 21:06:54,939 - INFO - Бот запущен и готов к работе
2024-10-14 21:06:54,942 - INFO - Start polling
2024-10-14 21:06:55,037 - INFO - Run polling for bot @sdfdsdgdf334dfsdf_bot id=7530574986 - 'Робот'
2024-10-14 21:07:35,908 - INFO - Text: As an AI, I don't have feelings or experiences like humans do. However, I'm here and ready to assist you! 

How are *you* doing today? 😊 

2024-10-14 21:07:35,911 - INFO - Phonemes: ['e1', 's', ' ', 'a', 'n', ' ', 'a', 'i', ',', ' ', 'i', ' ', 'd', 'o', 'n', "'", 't', ' ', 'h', 'a', 'v', 'e', ' ', 'f', 'e', 'e', 'l', 'i', 'n', 'g', 's', ' ', 'o', 'r', ' ', 'e', 'x', 'p', 'e', 'r', 'i', 'e', 'n', 'c', 'e', 's', ' ', 'l', 'i', 'k', 'e', ' ', 'h', 'u', 'm', 'a', 'n', 's', ' ', 'd', 'o', '.', ' ', 'h', 'o', 'w', 'e', 'v', 'e', 'r', ',', ' ', 'i', "'", 'm', ' ', 'h', 'e', 'r', 'e', ' ', 'e1', 'n', 'd', ' ', 'r', 'e', 'a', 'd', 'y', ' ', 't', 'o', ' ', 'a', 

In [ ]:
# такое сообщение было для моделей Silero (в итоге заменил Silero на Vosk)
# print(welcome_message)


__Привет, это бот помошник, варианты использования:__
1\) Отправь голосовое или текст чтобы получить ответ текстом и голосом
2\) Для изменения голоса озвучивания отправь число от 0 до 4:

 **0**: _aidar_
**1**: _baya_
**2**: _kseniya_
**3**: _xenia_
**4**: _eugene_



## Docker Speech-to-Speech Bot

Данный пример упрощен для запуска в Colab, так же упрощена структура Docker, итоговый проект находится в репозитории  
https://github.com/sergey21000/telegram-sst-tts-bot

**Сборка Docker образа для Телеграм бота**

---
Образы NVIDIA CUDA на DockerHub  
https://hub.docker.com/r/nvidia/cuda

Образы NVIDIA CUDA на NVIDIA  
https://catalog.ngc.nvidia.com/orgs/nvidia/containers/cuda

Образы Pytorch на DockerHub  
https://hub.docker.com/r/pytorch/pytorch/tags

Образы Pytorch на NVIDIA  
https://catalog.ngc.nvidia.com/orgs/nvidia/containers/pytorch/tags

---
Установка CUDA Toolkit (выбор любой платформы, в том числе WSL)  
https://developer.nvidia.com/cuda-downloads?target_os=Linux&target_arch=x86_64

Установка Container Toolkit чтобы Docker видел видеокарту  
https://docs.nvidia.com/datacenter/cloud-native/container-toolkit/latest/install-guide.html#installing-with-apt

*Проверка что все установлено и Docker видит видеокарту:*

```
docker run --rm --gpus all nvcr.io/nvidia/k8s/cuda-sample:nbody nbody -gpu -benchmark
```

---

**Структура проекта**
 - 📁 `model`
 - `Dockerfile-cpu`
 - `Dockerfile-cuda`
 - `app.py`
 - `config.py`
 - `requirements.txt`

---

**Сборка образа докер образа приложения чат-бота**  

**Сборка образа и запуск контейнера:**

1. Сборка образа  

 - с поддержкой CPU
```
docker build -t telegram-stt-tts-bot:cpu -f Dockerfile-cpu .
```

 - с поддержкой CUDA
```
docker build -t telegram-stt-tts-bot:cuda -f Dockerfile-cuda .
```

2. Запуск контейнера на 7860 порту с пробросом конфига модели и папки с моделью через `docker volumes`
 - с поддержкой CPU
```
docker run -it \
    -v ./llm_model:/app/llm_model \
    -v ./vosk_models:/app/vosk_models \
    -v ./config.py:/app/config.py \
    --env-file .env \
    telegram-stt-tts-bot:cpu
```

 - с поддержкой CUDA
```
docker run -it --gpus all \
    -v ./llm_model:/app/llm_model \
    -v ./vosk_models:/app/vosk_models \
    -v ./config.py:/app/config.py \
    --env-file .env \
    telegram-stt-tts-bot:cuda
```

---

Содержимое `Dockerfile-cpu`
```
FROM python:3.10

RUN apt-get update && apt-get install -y ffmpeg \
    && apt-get clean \
    && apt-get autoremove -y \
    && rm -rf /var/lib/apt/lists/*

WORKDIR /app
COPY requirements.txt .
RUN pip install --no-cache-dir -r requirements.txt
COPY main.py config.py handlers.py middlewares.py infer_models.py infer_utils.py .
CMD ["python3", "main.py"]
```
Несжатый образ занимает 1.75 GB

Содержимое `Dockerfile-cuda` для CUDA 12.4
```
FROM pytorch/pytorch:2.4.1-cuda12.4-cudnn9-devel AS builder

COPY requirements.txt .
RUN pip wheel --no-cache-dir --no-deps --wheel-dir /wheels $(grep -v '^torch' requirements.txt)

FROM pytorch/pytorch:2.4.1-cuda12.4-cudnn9-runtime
RUN apt-get update && apt-get install -y ffmpeg \
    && apt-get clean \
    && apt-get autoremove -y \
    && rm -rf /var/lib/apt/lists/*

WORKDIR /app
COPY --from=builder /wheels /wheels
RUN pip install --no-cache-dir /wheels/* && rm -rf /wheels

COPY main.py config.py .
CMD ["python3", "main.py"]
```
Несжатый образ занимает 4.34 GB

## Deploy Telegram Bots

**Деплой телеграм бота на сервис GoormIDE**  
На этом сервисе каждый месяц даются бесплатные кредиты (45 штук), которые можно потратить на эксперименты с деплоем проектов  
Например тариф `Medium` с 4 ядерным CPU и 4 GB ОЗУ стоит примерно 10 кредитов в час  
Данный пример создан для демонстрации процесса деплоя, так как он в целом везде одинаковый  

---

**Деплой Телеграм бота на сервис GoormIDE**  

1) Регистрация на https://ide.goorm.io/ (можно войти через Google почту)

2) Создание и запуск нового контейнера `New Container` -> `Blank` -> `Create` -> Выбрать тариф (например `Medium`) -> `Run`  
Чем лучше тариф тем быстрее будет работать, я выбрал `Medium`   
Вместо `Blank` можно выбрать `Nvidia Tesla T4`, тогда нужно будет просто изменить `--extra-index-url` при установке зависимостей

3) Установка `ffmpeg`
```
apt install -y ffmpeg
```

4) Создаем и активируем новое виртуальное окружение, в терминале вводим  
```
apt install python3.12-venv
python3 -m venv env
source env/bin/activate
```
Надпись в терминале должна сменится с `root@goorm` на `(env) root@goorm`

5) Создаем файл `requirements.txt`, обновляем `pip` и устанавливаем библиотеки
```
pip install -U pip
pip install -r requirements.txt --extra-index-url https://download.pytorch.org/whl/cpu
pip cache purge
```
Для установки библиотек с поддержкой CUDA заменить строчку 2 на  
`pip install -r requirements.txt --extra-index-url https://download.pytorch.org/whl/cu124`

5) Создаем файлы `main.py` и `config.py` (любое имя), записываем туда код бота.  
Или перекидываем их через `File` -> `Import` -> `File`  
Не забываем сохранять файл (`Ctrl + S`), если делаем какие либо правки в коде  
Файл с токеном бота можно `.env` можно создать тут же, а можно передать через переменные оркужения (нажать на шестеренку около контейнера на главной странице и установить `Environment variable`)

6) Запускаем бота из терминала командой `python3 main.py`  

*Первый запуск будет долгим из за загрузки моделей*  

# Overview of stages

**Обзор этапов преобразования генерации текста из текста, преобразования текста в речь и речи в текст**

## Text-to-Text

**Генерация текста из текста с использованием LLM**

Новый способ инициализации модели - напрямую из репозитория HF  
https://github.com/abetlen/llama-cpp-python/blob/main/examples/gradio_chat/local.py

In [ ]:
# параметры инициализации модели
MODEL_KWARGS = dict(
    repo_id='bartowski/gemma-2-2b-it-GGUF',  # название репозитория модели на HF
    filename='*8_0.gguf',  # название файла модели из репозитория HF или регулярка для него
    local_dir='models',  # путь куда скачивтаь модель (будет создана папка)
    n_gpu_layers=-1,  # использовать все слои ГПУ если ГПУ доступен
    verbose=False,  # выводить инфо о модели при инициализации (False чтобы ничего не выводить)
)

# инициализация модели для генерации текста моделью в формате GGUF
model = Llama.from_pretrained(**MODEL_KWARGS)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:81: UserWarning: 
Access to the secret `HF_TOKEN` has not been granted on this notebook.
You will not be requested again.
Please restart the session if you want to be prompted again.
  warnings.warn(


gemma-2-2b-it-Q8_0.gguf:   0%|          | 0.00/2.78G [00:00<?, ?B/s]

Поддерживает ли модель системный промт

In [ ]:
model.metadata['tokenizer.chat_template']

"{{ bos_token }}{% if messages[0]['role'] == 'system' %}{{ raise_exception('System role not supported') }}{% endif %}{% for message in messages %}{% if (message['role'] == 'user') != (loop.index0 % 2 == 0) %}{{ raise_exception('Conversation roles must alternate user/assistant/user/assistant/...') }}{% endif %}{% if (message['role'] == 'assistant') %}{% set role = 'model' %}{% else %}{% set role = message['role'] %}{% endif %}{{ '<start_of_turn>' + role + '\n' + message['content'] | trim + '<end_of_turn>\n' }}{% endfor %}{% if add_generation_prompt %}{{'<start_of_turn>model\n'}}{% endif %}"

In [ ]:
# проверка что в шаблоне токенайзера нет исключения System role not supported
SUPPORT_SYSTEM_ROLE = 'System role not supported' not in model.metadata['tokenizer.chat_template']
SUPPORT_SYSTEM_ROLE

False

Генерация текста моделью (по одному токену с параметром `stream=True`)

Документация по методу `create_chat_completion`  
https://llama-cpp-python.readthedocs.io/en/latest/api-reference/#llama_cpp.Llama.create_chat_completion

In [ ]:
%%time

# системный промт
system_prompt = 'Отвечай максимально кратко и простым языком, если не знаешь ответ, говори - "Я не знаю"'
# входной запрос пользователя
user_message = 'Почему коровы летают вверх ногами?'
# список с репликами юзера и бота
messages = []

# если задан системынй промт и модель его поддерживает - добавить его в начало списка messages
if system_prompt and SUPPORT_SYSTEM_ROLE:
    messages.append({'role': 'system', 'content': system_prompt})

# добавление сообщения пользователя в список
messages.append({'role': 'user', 'content': user_message})

# параметры генерации
# чтобы модель отвечала одинаково достаточно поставить top_k=1, top_p=0 и repeat_penalty=1 не зависимо от остальных параметров
GENERATION_KWARGS = dict(
    temperature=1,  # температура для софтмакса
    top_p=0.0,  # сумма вероятностей токенов из которых нужно выбирать следующий токен
    top_k=1,  # из скольки максимально вероятных токенов выбирать следующий токен
    repeat_penalty=1.0,  # штраф модели за повторения
    )

# создание объекта итератора для генерации текста
# при итерации по этому объекту в цикле она будет возвращать сгенерированный текст частями
stream_response = model.create_chat_completion(
    messages=messages,  # входной промт на который надо сгенерировать ответ
    stream=True,  # вернуть генератор
    **GENERATION_KWARGS,  # параметры генерации
    )

# пустую строку будем конкатенировать с токенами ответа модели
response_text = ''
# итерация и последовательная генерация текста моделью в цикле
for chunk in stream_response:
    # извлечение текущего сгенерированного токена
    token = chunk['choices'][0]['delta'].get('content')
    if token is not None:
        response_text += token
        print(token, end='')

Коровы не летают вверх ногами! 😄 

Это просто шутка или забавный миф. Коровы - это животные, которые живут на земле и не умеют летать. 

Может быть, ты слышал эту фразу в каком-то рассказе или фильме? 
CPU times: user 29.1 s, sys: 23.3 ms, total: 29.1 s
Wall time: 28.9 s


Проверка генерации с историей сообщений (на случай если нужно сделать поддержку истории сообщений)

In [ ]:
%%time

# какое кол-во сообщений в истории учитывать
history_len = 1
# история переписки пользователя и бота
history = [
    {'role': 'user', 'content': 'Что ты умеешь?'},
    {'role': 'assistant', 'content': 'Ничего'},
]
# системный промт
system_prompt = ''
# входной запрос пользователя - проверка что модель так же получает на вход историю сообщений
user_message = 'Что я спросил и что ты ответила одно сообщение назад?'

# список с репликами юзера и бота
messages = []

# если задан системынй промт и он поддерживается моделью - добавить его в начало списка
if system_prompt and SUPPORT_SYSTEM_ROLE:
    messages.append({'role': 'system', 'content': system_prompt})

# дабвление history_len последних реплик эзера и бота
if history_len != 0:
    messages.extend(history[-(history_len*2):])

# формирование стандартного промта с запросом от пользователя
messages.append({'role': 'user', 'content': user_message})

# параметры генерации
# чтобы модель отвечала одинаково достаточно поставить top_k=1, top_p=0 и repeat_penalty=1 не зависимо от остальных параметров
GENERATION_KWARGS = dict(
    temperature=1,  # температура для софтмакса
    top_p=0.0,  # сумма вероятностей токенов из которых нужно выбирать следующий токен
    top_k=1,  # из скольки максимально вероятных токенов выбирать следующий токен
    repeat_penalty=1.0,  # штраф модели за повторения
    )

# создание объекта итератора для генерации текста
# при итерации по этому объекту в цикле она будет возвращать сгенерированный текст частями
stream_response = model.create_chat_completion(
    messages=messages,  # входной промт на который надо сгенерировать ответ
    stream=True,  # вернуть генератор
    **GENERATION_KWARGS,  # параметры генерации
    )

# пустую строку будем конкатенировать с токенами ответа модели
response_text = ''
# итерация и последовательная генерация текста моделью в цикле
for chunk in stream_response:
    # извлечение текущего сгенерированного токена
    token = chunk['choices'][0]['delta'].get('content')
    if token is not None:
        response_text += token
        print(token, end='')

Ты спросил, что я умею, а я ответила, что "ничего". 

Я немного не понимаю, что ты имеешь в виду.  Может, ты хотел спросить что-то другое? 
CPU times: user 19.3 s, sys: 59.8 ms, total: 19.4 s
Wall time: 22.1 s


Генерация текста моделью без стриминга

In [ ]:
%%time

GENERATION_KWARGS = dict(
    temperature=1,  # температура для софтмакса
    top_p=0.0,  # сумма вероятностей токенов из которых нужно выбирать следующий токен
    top_k=1,  # из скольки максимально вероятных токенов выбирать следующий токен
    repeat_penalty=1.0,  # штраф модели за повторения
    )
messages = [{'role': 'user', 'content': 'Как дела?'}]
response = model.create_chat_completion(messages=messages, **GENERATION_KWARGS)

CPU times: user 9.53 s, sys: 18.9 ms, total: 9.54 s
Wall time: 12.3 s


In [ ]:
response

{'id': 'chatcmpl-d084423b-ca09-425a-a565-9cefdf47beb3',
 'object': 'chat.completion',
 'created': 1728938835,
 'model': 'models/gemma-2-2b-it-Q8_0.gguf',
 'choices': [{'index': 0,
   'message': {'role': 'assistant',
    'content': 'У меня все отлично! 😊  Как у тебя дела? \n'},
   'logprobs': None,
   'finish_reason': 'stop'}],
 'usage': {'prompt_tokens': 12, 'completion_tokens': 14, 'total_tokens': 26}}

In [ ]:
generated_text = response['choices'][0]['message']['content']
generated_text

'У меня все отлично! 😊  Как у тебя дела? \n'

Функция для генерации текста

In [ ]:
# функция для генерации текста моделью
def generate_text(user_message: str, system_prompt: str, generation_kwargs: dict):
    # формирование входа для модели - список с диалогом юзера и бота
    messages = []
    # добавления системного промта если он есть
    if system_prompt and SUPPORT_SYSTEM_ROLE:
        messages.append({'role': 'system', 'content': system_prompt})
    # добавление ткущего запроса пользователя
    messages.append({'role': 'user', 'content': user_message})
    # генерация ответа моделью
    response = model.create_chat_completion(
        messages=messages,  # входной промт на который надо сгенерировать ответ
        **generation_kwargs,  # параметры генерации
        )
    generated_text = response['choices'][0]['message']['content']
    return generated_text

Проверка функции

In [ ]:
%%time

# конфиг для генерации
GENERATION_KWARGS = dict(
    temperature=1,  # температура для софтмакса
    top_p=0.0,  # сумма вероятностей токенов из которых нужно выбирать следующий токен
    top_k=1,  # из скольки максимально вероятных токенов выбирать следующий токен
    repeat_penalty=1.0,  # штраф модели за повторения
    )

# проверка генерации
message = 'Как дела?'
system_prompt = ''
generated_text = generate_text(message, system_prompt, GENERATION_KWARGS)
print(generated_text)

У меня всё отлично! 😊  Как у тебя дела? 

CPU times: user 7.1 s, sys: 10.2 ms, total: 7.11 s
Wall time: 7.39 s


## Text-to-Speech

**Преобразование текста в речь - краткий обзор трех библиотек - vosk-tts, Silero и TerraTTS (в итоге выбрал vosk)**

---

1) Вариант через библиотеку `vosk-tts`

Страница библиотеки на Github  
https://github.com/alphacep/vosk-tts

Установка библиотеки  

In [ ]:
!pip install vosk-tts

Инициализация модели

In [ ]:
from vosk_tts import Model, Synth

model = Model(model_name='vosk-model-tts-ru-0.7-multi')
synth = Synth(model)

Ситез речи из текста

In [ ]:
%%time

audio_path_tts = 'out.wav'
text = 'Привет, ну че, пойдем гулять?'
synth.synth(text, audio_path_tts, speaker_id=2)

CPU times: user 859 ms, sys: 88.8 ms, total: 948 ms
Wall time: 744 ms


Отображение результата

In [ ]:
Audio(audio_path_tts)

Проверка всех голосов

In [ ]:
%%time

audio_path_tts = 'out.wav'
text = 'Привет, ну че, пойдем гулять?'

for speaker_id in range(5):
    synth.synth(text, audio_path_tts, speaker_id=speaker_id)
    display(Audio(audio_path_tts))

CPU times: user 5.57 s, sys: 18.7 ms, total: 5.59 s
Wall time: 6.08 s


In [ ]:
# конфиг модели
synth.model.config

{'audio': {'sample_rate': 22050},
 'inference': {'noise_level': 0.5,
  'speech_rate': 1,
  'duration_noise_level': 0.8},
 'phoneme_map': {},
 'phoneme_id_map': {'_': [0],
  '^': [1],
  '$': [2],
  ' ': [3],
  '!': [4],
  "'": [5],
  '(': [6],
  ')': [7],
  ',': [8],
  '-': [9],
  '.': [10],
  ':': [11],
  ';': [12],
  '?': [13],
  'a0': [14],
  'a1': [15],
  'b': [16],
  'bj': [17],
  'c': [18],
  'ch': [19],
  'd': [20],
  'dj': [21],
  'e0': [22],
  'e1': [23],
  'f': [24],
  'fj': [25],
  'g': [26],
  'gj': [27],
  'h': [28],
  'hj': [29],
  'i0': [30],
  'i1': [31],
  'j': [32],
  'k': [33],
  'kj': [34],
  'l': [35],
  'lj': [36],
  'm': [37],
  'mj': [38],
  'n': [39],
  'nj': [40],
  'o0': [41],
  'o1': [42],
  'p': [43],
  'pj': [44],
  'r': [45],
  'rj': [46],
  's': [47],
  'sch': [48],
  'sh': [49],
  'sj': [50],
  't': [51],
  'tj': [52],
  'u0': [53],
  'u1': [54],
  'v': [55],
  'vj': [56],
  'y0': [57],
  'y1': [58],
  'z': [59],
  'zh': [60],
  'zj': [61]},
 'num_symbol

2) Вариант через библиотеку `Silero`

Модели для синтеза речи Silero  
https://github.com/snakers4/silero-models  
Статья на хабре  
https://habr.com/ru/articles/660565/

Установка бибилотек для работы Silero

In [ ]:
!pip install -q torchaudio omegaconf

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.0/117.0 kB 7.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.5/79.5 kB 5.6 MB/s eta 0:00:00


Инициализация модели через Torch Hub

In [ ]:
import torch

# выбор языка и модели из списка https://github.com/snakers4/silero-models#text-to-speech
language = 'ru'
model_id = 'v4_ru'

# загрузка модели из torchhub
model_tts, example_text = torch.hub.load(
    repo_or_dir='snakers4/silero-models',
    model='silero_tts',
    language=language,
    speaker=model_id,
    trust_repo=True,
    )

Downloading: "https://github.com/snakers4/silero-models/zipball/master" to /root/.cache/torch/hub/master.zip
100%|██████████| 38.2M/38.2M [00:02<00:00, 13.4MB/s]


In [ ]:
# какие есть голоса
model_tts.speakers

['aidar', 'baya', 'kseniya', 'xenia', 'eugene', 'random']

Ситез речи из текста

In [ ]:
%%time

# текст который надо перевести в речь
text = 'Привет, ну че, пойдем гулять?'

# частота дискретизации (качество звука) (8000, 24000, 48000)
sample_rate = 24000

# синтезировать речь из текста и сохранить аудио на диск по пути audio_path_tts
audio_path_tts = model_tts.save_wav(
    text=text,
    speaker=model_tts.speakers[3],  # выбранный голос из списка model.speakers
    sample_rate=sample_rate,
    put_accent=True,  # делать ли акцент и еще какая то настройка
    put_yo=True,
    )
audio_path_tts

CPU times: user 10.8 s, sys: 741 ms, total: 11.6 s
Wall time: 20.7 s


'test.wav'

Отобразить аудио в колаб

In [ ]:
Audio(audio_path_tts, rate=sample_rate)

---

3) Вариант через библиотеку `TeraTTS`

Страница билиотеки на GitHub   
https://github.com/Tera2Space/TeraTTS

Репозиторий с моделями  
https://huggingface.co/TeraTTS

Демо приложение  
https://huggingface.co/spaces/TeraTTS/TTS

Клонирование репозитория

In [ ]:
!git clone https://huggingface.co/spaces/TeraTTS/TTS

Cloning into 'TTS'...
remote: Enumerating objects: 163, done.
remote: Total 163 (delta 0), reused 0 (delta 0), pack-reused 163 (from 1)
Receiving objects: 100% (163/163), 30.16 KiB | 7.54 MiB/s, done.
Resolving deltas: 100% (84/84), done.


Переход в папку склонированного репозитория

In [ ]:
%cd /content/TTS

/content/TTS


Установка бибилотек (и перезапуск среды в Colab)  
Важно - после этой установки версия `transformers` понизится и некоторые модели LLM (напрмиер Qwen 2+) не будут работать

In [ ]:
!pip install -r requirements.txt

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.3/85.3 kB 7.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.0/35.0 MB 15.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.6/101.6 kB 8.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.3/15.3 MB 75.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of transformers to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.7/43.7 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
%cd /content/TTS

/content/TTS


Инициализация модели

In [ ]:
from IPython.display import Audio, display
from infer_onnx import TTS
from ruaccent import RUAccent

# выбор модели
model_names = ['TeraTTS/natasha-g2p-vits', 'TeraTTS/glados2-g2p-vits', 'TeraTTS/glados-g2p-vits', 'TeraTTS/girl_nice-g2p-vits']
model_name = model_names[0]

# инициализация модели
model = TTS(model_name)

Fetching 3 files:   0%|          | 0/3 [00:00<?, ?it/s]

Use g2p


Предварительная обработка текста (расстановка ударений и тд, опционально)

In [ ]:
# загрузка и инициализация модели для предобработки текста
accentizer = RUAccent()
accentizer.load(omograph_model_size='turbo3.1', use_dictionary=True)

In [ ]:
# текст который надо озвучить
text = 'Здравствуйте, это пробный запуск.'

# предобработка текста (ударения, ё)
text = accentizer.process_all(text)
text

'Здр+авствуйте, +это пр+обный з+апуск.'

Преобразование текста в речь

In [ ]:
%%time

# параметр увеличения длины звучания (по учмолчанию 1.2)
length_scale = 1.2

# преобразование текста в речь (возвращает массив numpy)
audio = model(text, length_scale=length_scale)

# сохранение результата на диск
model.save_wav(audio, 'temp.wav', sample_rate=model.config['samplerate'])

CPU times: user 2.55 s, sys: 31.8 ms, total: 2.58 s
Wall time: 2.65 s


In [ ]:
Audio('temp.wav')

Увеличение длины звучания

In [ ]:
%%time

length_scale = 1.8
audio = model(text, length_scale=length_scale)
display(Audio(audio, rate=model.config['samplerate']))

CPU times: user 2.48 s, sys: 31.9 ms, total: 2.52 s
Wall time: 2.53 s


Проверка всех голосов (с предобработкой текста)

In [ ]:
# загрузка и инициализация модели для предобработки текста
accentizer = RUAccent()
accentizer.load(omograph_model_size='turbo3.1', use_dictionary=True)

In [ ]:
%%time

# синтез речи с перебором моделей
text = 'Доброе утро, как ваши дела, как поживаете?'
text = accentizer.process_all(text)
model_names = ['TeraTTS/natasha-g2p-vits', 'TeraTTS/glados2-g2p-vits', 'TeraTTS/glados-g2p-vits', 'TeraTTS/girl_nice-g2p-vits']
length_scale = 1.2

for model_name in model_names:
    model = TTS(model_name)
    audio = model(text, length_scale=length_scale)
    display(Audio(audio, rate=model.config['samplerate']))

Use g2p


Fetching 3 files:   0%|          | 0/3 [00:00<?, ?it/s]

Use g2p


Fetching 3 files:   0%|          | 0/3 [00:00<?, ?it/s]

Use g2p


Fetching 3 files:   0%|          | 0/3 [00:00<?, ?it/s]

Use g2p


CPU times: user 50.1 s, sys: 4.55 s, total: 54.6 s
Wall time: 1min 8s


Проверка без предобработки текста

In [ ]:
# инициализацуя модели
model_name = 'TeraTTS/natasha-g2p-vits'
model = TTS(model_name)

Use g2p


In [ ]:
%%time

# синтез речи
text = 'Доброе утро, как ваши дела, как поживаете?'
length_scale = 1.2
audio = model(text, length_scale=length_scale)
display(Audio(audio, rate=model.config['samplerate']))

CPU times: user 3.39 s, sys: 145 ms, total: 3.54 s
Wall time: 3.3 s


In [ ]:
%cd /content

/content


## Speech-to-Text

Загрузка примера аудио с речью из датасета RusNews  
https://huggingface.co/datasets/toloka/VoxDIY-RusNews


In [ ]:
import requests

# загрузить аудио в виде байтов
audio_url = 'https://tlk.s3.yandex.net/annotation_tasks/russian/1034.wav'
audio_bytes = requests.get(audio_url).content

# и сохранить на диске
audio_path = 'example.wav'
with open(audio_path, 'wb') as file:
    file.write(audio_bytes)

# отобразить в колабе
Audio(audio_path)

---

**Автоматическое распознавание речи (Automatic Speech Recognition, ASR, STT) с использованием библиотеки Vosk**  

Страница библиотеки Vosk на Github  
https://github.com/alphacep/vosk-api/

Документация  
https://alphacephei.com/vosk/index.ru

Примеры распознавания  
https://github.com/alphacep/vosk-api/tree/master/python/example

Загрузка и распаковка архива с моделью  
Все модели  
https://alphacephei.com/vosk/models

In [ ]:
!wget -qq --show-progress https://alphacephei.com/vosk/models/vosk-model-small-ru-0.22.zip

vosk-model-small-ru 100%[===================>]  44.09M  17.5MB/s    in 2.5s    


In [ ]:
!unzip -q vosk-model-small-ru-0.22.zip

Инициализация модели

In [ ]:
import json
import wave
from vosk import Model as ModelSTT, KaldiRecognizer

# инициализация модели для распознавания речи
vosk_model_dir = '/content/vosk-model-small-ru-0.22'
model_stt = ModelSTT(vosk_model_dir)

Распознавание речи в текст

In [ ]:
%%time

# открытие аудиофайла и получение его частоты дискретизации
wf = wave.open(audio_path, 'rb')
sample_rate = wf.getframerate()

# создание распознавателя
recognizer = KaldiRecognizer(model_stt, sample_rate)

# чтение аудиофайла байтами частями и распознавание речи в текст
result = ""
while True:
    audio_data = wf.readframes(4000)
    if len(audio_data) == 0:
        break
    if recognizer.AcceptWaveform(audio_data):
        result += recognizer.Result()
        print(result)

# получение окончательного результата (здесь происходит все распознавание)
result += recognizer.FinalResult()
recognized_text = json.loads(result)['text']
print(recognized_text)

он лишь говорит что ни в чем не виноват и в отставку уходить не собирается
CPU times: user 1.11 s, sys: 19.7 ms, total: 1.13 s
Wall time: 1.21 s


Короткий вариант что происходит

In [ ]:
# чтение аудио файла
wf = wave.open(audio_path, 'rb')
# получение аудио байтов
audio_data = wf.readframes(-1)
# получение частоты дискретизации
sample_rate = wf.getframerate()
# инициализация рапознавателя текста из речи
recognizer = KaldiRecognizer(model_stt, sample_rate)
# нужно вызвать этот метод перед следующим
recognizer.AcceptWaveform(audio_data)
# получение результата в виде json строки
recognizer.FinalResult()

'{\n  "text" : "он лишь говорит что ни в чем не виноват и в отставку уходить не собирается"\n}'

In [ ]:
def speech_to_text(audio_path: str) -> str:
    # чтение аудио файла
    wf = wave.open(audio_path, 'rb')
    # получение аудио байтов
    audio_data = wf.readframes(-1)
    # получение частоты дискретизации
    sample_rate = wf.getframerate()
    # инициализация рапознавателя текста из речи
    recognizer = KaldiRecognizer(model_stt, sample_rate)
    # нужно вызвать этот метод перед следующим
    recognizer.AcceptWaveform(audio_data)
    # получение результата в виде json строки
    recognized_text = json.loads(recognizer.FinalResult())['text']
    return recognized_text

recognized_text = speech_to_text(audio_path)
recognized_text

'он лишь говорит что ни в чем не виноват и в отставку уходить не собирается'

---

**Автоматическое распознавание речи (Automatic Speech Recognition, ASR, STT) с использованием библиотеки Speech Recognition**  

Страница библиотеки SpeechRecognition на Github  
https://github.com/Uberi/speech_recognition

Установка SpeechRecognition

In [ ]:
!pip install -q SpeechRecognition

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.8/32.8 MB 48.8 MB/s eta 0:00:00


In [ ]:
import speech_recognition as sr

Распознавание текста из речи

In [ ]:
%%time

# объект распознавантеля речи
recognizer = sr.Recognizer()

# cчитываем аудио
with sr.AudioFile(audio_path) as source:
    audio = recognizer.record(source)

# пробуем достать из аудио текст
try:
    recognize_text = recognizer.recognize_google(audio, language='ru')
# если какая то ошибка то возвращаем None
except Exception as ex:
    print(f'Не удалось распознать аудиофрагмент. Код ошибки: {ex}')
    recognize_text = None

recognize_text

CPU times: user 16.4 ms, sys: 956 µs, total: 17.4 ms
Wall time: 466 ms


'он лишь говорит что ни в чём не виноват и в отставку уходить не собирается'

Функция для распознавания речи библиотекой SpeechRecognition

In [ ]:
# принимает путь до айдио файла и извлекает из него текст речи
# если речь не обнаружена или еще какая ошибка - возвращает None
def speech_to_text(audio_path: str) -> str:
    recognizer = sr.Recognizer()
    with sr.AudioFile(audio_path) as source:
        audio = recognizer.record(source)
    try:
        recognize_text = recognizer.recognize_google(audio, language='ru')
    except Exception as ex:
        print(f'Не удалось распознать аудиофрагмент. Код ошибки: {ex}')
        recognize_text = None
    return recognize_text

## Speech-to-Speech

**Генерация речи из речи с использованием предыдущих решений**

Функция для загрузки и распаковки архивов с моделями STT и TTS

In [ ]:
import zipfile
import urllib.request

# функция для загрузки и распаковки архивов с моделями STT и TTS
def download_and_extract_zip(url):
    zip_path, _ = urllib.request.urlretrieve(url)
    with zipfile.ZipFile(zip_path, 'r') as file:
        file.extractall()

# ссылки на архивы с моделями
tts_model_url = 'https://alphacephei.com/vosk/models/vosk-model-tts-ru-0.7-multi.zip'
stt_model_url = 'https://alphacephei.com/vosk/models/vosk-model-small-ru-0.22.zip'

# папки куда распакуются папки из архивов
tts_model_dir = Path(tts_model_url).stem
stt_model_dir = Path(stt_model_url).stem

# если модели еще не скачаны то загрузить и распаковать
if not Path(stt_model_dir).is_dir() or not Path(tts_model_dir).is_dir():
    print('Загрузка модели TTS')
    download_and_extract_zip(tts_model_url)
    print('Загрузка модели STT')
    download_and_extract_zip(stt_model_url)

Загрузка модели TTS
Загрузка модели STT


Инициализация всех моделей

In [ ]:
from vosk_tts import Model as ModelTTS, Synth
from vosk import Model as ModelSTT, KaldiRecognizer

# инициализация модели для синтеза речи
model_tts = ModelTTS(model_path=tts_model_dir)
synth = Synth(model_tts)

# инициализация модели для распознавания речи
model_stt = ModelSTT(stt_model_dir)
sample_rate = 24000
recognizer = KaldiRecognizer(model_stt, sample_rate)

# инициализация пайплайна для генерации ответа
# параметры инициализации модели
MODEL_KWARGS = dict(
    repo_id='bartowski/gemma-2-2b-it-GGUF',  # название репозитория модели на HF
    filename='*8_0.gguf',  # название файла модели из репозитория HF или регулярка для него
    local_dir='models',  # путь куда скачивтаь модель (будет создана папка)
    n_gpu_layers=-1,  # использовать все слои ГПУ если ГПУ доступен
    verbose=False,  # выводить инфо о модели при инициализации (False чтобы ничего не выводить)
)

# инициализация модели для генерации текста моделью в формате GGUF
model = Llama.from_pretrained(**MODEL_KWARGS)
SUPPORT_SYSTEM_ROLE = 'System role not supported' not in model.metadata['tokenizer.chat_template']

Загрузка примера аудио с речью из датасета RusNews  
https://huggingface.co/datasets/toloka/VoxDIY-RusNews


In [ ]:
import requests

# загрузить аудио в виде байтов
audio_url = 'https://tlk.s3.yandex.net/annotation_tasks/russian/1034.wav'
audio_bytes = requests.get(audio_url).content

# и сохранить на диске
audio_path = 'example.wav'
with open(audio_path, 'wb') as file:
    file.write(audio_bytes)

# отобразить в колабе
Audio(audio_path)

Функции для преобразования человеческой речи в текст, генерации ответа на текст, и преобразования его в ситезированную речь

In [ ]:
# принимает путь до айдио файла и извлекает из него текст речи
# если речь не обнаружена или еще какая ошибка - возвращает None
def speech_to_text(audio_path: str) -> str:
    # чтение аудио файла
    wf = wave.open(audio_path, 'rb')
    # получение аудио байтов
    audio_data = wf.readframes(-1)
    # получение частоты дискретизации
    sample_rate = wf.getframerate()
    # инициализация рапознавателя текста из речи
    recognizer = KaldiRecognizer(model_stt, sample_rate)
    # нужно вызвать этот метод перед следующим
    recognizer.AcceptWaveform(audio_data)
    # получение результата в виде json строки
    recognized_text = json.loads(recognizer.FinalResult())['text']
    return recognized_text


# генерирует новый текст из полученного recognized_text
def text_to_text(user_message: str, system_prompt: str, generation_kwargs: dict):
    # формирование входа для модели - список с диалогом юзера и бота
    messages = []
    # добавления системного промта если он есть
    if system_prompt and SUPPORT_SYSTEM_ROLE:
        messages.append({'role': 'system', 'content': system_prompt})
    # добавление ткущего запроса пользователя
    messages.append({'role': 'user', 'content': user_message})
    # генерация ответа моделью
    response = model.create_chat_completion(
        messages=messages,  # входной промт на который надо сгенерировать ответ
        **generation_kwargs,  # параметры генерации
        )
    generated_text = response['choices'][0]['message']['content']
    return generated_text


# преобразует текст в речь, возвращает путь до аудиофайла с речью
# принимает текст а так же порядковый номер голоса
def text_to_speech(generated_text: str, speaker_index: int)-> str:
    audio_path_tts = 'out.wav'
    synth.synth(generated_text, audio_path_tts, speaker_id=speaker_index)
    return audio_path_tts


# преобразует речь текст, генерирует ответ на него и синтезирует новую речь, используя функции выше
# принимает путь до исходной речи, а так же параметры генерации текста generation_kwargs
# возвращет путь до аудио с синтезированной речью, а так же текст этой речи
# если преобразование исходной речи в текст не сработало, возвращает None
def speech_to_speech(
        audio_path: str,
        system_prompt: str,
        generation_kwargs: dict,
        speaker_index: int,
        ) -> tuple[str | None, str | None]:
    recognized_text = speech_to_text(audio_path)
    if recognized_text.strip() == '':
        return None, None
    generated_text = text_to_text(recognized_text, system_prompt, generation_kwargs)
    audio_path_tts = text_to_speech(generated_text, speaker_index)
    return audio_path_tts, generated_text

Проверка работы функций

In [ ]:
%%time

# системный промт
SUSTEM_PROMPT = ''

# конфиг для генерации текста
GENERATION_KWARGS = dict(
    temperature=0.2,  # температура для софтмакса
    top_p=0.95,  # сумма вероятностей токенов из которых нужно выбирать следующий токен
    top_k=40,  # из скольки максимально вероятных токенов выбирать следующий токен
    repeat_penalty=1.0,  # штраф модели за повторения
    )

# проверка работы функции
audio_path_tts, generated_text = speech_to_speech(audio_path, SUSTEM_PROMPT, GENERATION_KWARGS, speaker_index=2)
print(generated_text)

In [ ]:
# отобразить в колаб
Audio(audio_path_tts)